In [4]:
aois = ["Bab el-Mandeb Strait", "Cape of Good Hope", "Suez Canal"]
countries_of_interest = [
    "Egypt",
    "Yemen",
    "Djibouti",
    "Eritrea",
    "Saudi Arabia",
    "Jordan",
]
ISO_COUNTRIES = [818, 887, 262, 232, 682, 400]
START_DATE = "2023-10-07"

In [175]:
%reload_ext autoreload
%autoreload 2
import logging

import os

import pandas as pd

from acled_conflict_analysis import extraction
from acled_conflict_analysis import visuals
from acled_conflict_analysis import analysis
# from red_sea_monitoring.acled import *

from datetime import date
from datetime import datetime


logger = logging.getLogger()
logging.basicConfig(format="%(asctime)s %(message)s", level=logging.INFO)

from plotnine import *

# Conflict in the Red Sea

This section examines how the conflict fatalities in the countries of the red sea region have progressed since the crisis started in October 7th. The analysis is conducted using dat from ACLED. 

## Insights

To match the conflict analysis with the maritime trade trends as [previously seen on this web-book](https://datapartnership.org/red-sea-monitoring/notebooks/ports/README.html), we aggregated the ACLED data to show weekly trends near the ports of interest. 

### Visualizing conflict fatalities between October 7th 2023 and October 20th 2024

In [7]:
data = extraction.acled_api(
    email_address=os.environ.get("ACLED_EMAIL"),
    access_key=os.environ.get("ACLED_KEY"),
    countries=countries_of_interest,
    start_date=START_DATE,
    end_date=date.today().isoformat(),
)

c:\WBG\Anaconda3\envs\data-goods\Lib\site-packages\urllib3\connectionpool.py:1103: InsecureRequestWarning: Unverified HTTPS request is being made to host 'api.acleddata.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings


In [8]:
analysis.data_type_conversion(data)

In [9]:
data.drop_duplicates(inplace=True)

In [28]:
south_red_sea = data[
    (data["event_type"] != "Protests") & (data["location"] == "South Red Sea")
]
south_red_sea = analysis.convert_to_gdf(south_red_sea)
conflict_red_sea = analysis.get_acled_by_group(
    south_red_sea, ["event_type", "location"], freq="D"
)

In [32]:
houthi_attacks = data[
    (data["event_type"] != "Protests") & (data["notes"].str.contains("Houthi"))
]
# analysis.get_acled_by_group(houthi_attacks, columns=['latitude', 'longitude', 'notes'], freq='D')
# houthi_attacks = analysis.convert_to_gdf(houthi_attacks)
conflict_houthi = analysis.get_acled_by_group(
    houthi_attacks, ["event_type", "sub_event_type", "location"], freq="W"
)

In [21]:
grouped_data = analysis.convert_to_gdf(
    houthi_attacks.groupby(
        [
            "latitude",
            "longitude",
            "notes",
            "event_type",
            "location",
            "country",
            "event_date",
        ]
    )["fatalities"]
    .agg(["sum", "count"])
    .reset_index()
)
grouped_data.rename(columns={"sum": "nrFatalities", "count": "nrEvents"}, inplace=True)

In [25]:
def split_in_three(text):
    # Step 1: Find the length of the text and divide into thirds
    third = len(text) // 3

    # Step 2: Find the closest space to the first third
    if " " in text[third:]:
        first_split_point = third + text[third:].find(" ")
    elif " " in text[:third]:
        first_split_point = text[:third].rfind(" ")
    else:
        first_split_point = third  # If no spaces, just split at third point

    # Step 3: Find the closest space to the second third
    if " " in text[first_split_point + third :]:
        second_split_point = (
            first_split_point + third + text[first_split_point + third :].find(" ")
        )
    elif " " in text[first_split_point:]:
        second_split_point = first_split_point + text[first_split_point:].rfind(" ")
    else:
        second_split_point = (
            first_split_point + third
        )  # If no spaces, just split at second third point

    # Step 4: Return the three parts
    return (
        text[:first_split_point],
        text[first_split_point:second_split_point],
        text[second_split_point:],
    )


# Apply the split_in_three function to the 'notes' column
grouped_data[["notes_part1", "notes_part2", "notes_part3"]] = (
    grouped_data["notes"].apply(lambda x: split_in_three(x)).apply(pd.Series)
)

In [22]:
events_dict = {
    datetime(2023, 10, 7): "First Attack on Gaza",
    datetime(2023, 11, 17): "First Attack on the Red Sea",
    # datetime(2022, 10,5): 'West Azerbaijan\nEarthquake',
}

In [26]:
m = grouped_data.explore(
    column="nrEvents",
    zoom_start=5.1,
    marker_kwds={"radius": 5},
    vmin=1,
    vmax=50,
    cmap="viridis",
    tooltip=["event_date", "location", "notes_part1", "notes_part2", "notes_part3"],
    tooltip_kwds={"aliases": ["date", "location", "details", "", ""]},
)
m

In [35]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from bokeh.models import Tabs

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}

show(
    visuals.get_bar_chart(
        conflict_houthi,
        "Reported Weekly Attacks involving Houthi forces",
        "All incidents were reported in the Yemen region. The sub event types that were identified in these attacks are Armed clash, Air/drone strike, Remote explosive/landmine/IED, \nShelling/artillery/missile attack, Arrests,Change to group/activity, Disrupted weapons use, Abduction/forced disappearance\nSource: ACLED",
        subtitle="",
        category=None,
        measure="nrEvents",
        color_code=measure_colors["nrEvents"],
        category_value="Yemen",
        events_dict=events_dict,
    )
)

Loading BokehJS ...

In [45]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}

show(
    visuals.get_bar_chart(
        conflict_red_sea,
        "Reported Attacks in the Red Sea Region",
        "All incidents were reported in the Yemen region. The sub event types that were identified in these attacks are Armed clash, Air/drone strike, Remote explosive/landmine/IED, \nShelling/artillery/missile attack, Arrests,Change to group/activity, Disrupted weapons use, Abduction/forced disappearance\nSource: ACLED",
        subtitle="",
        category=None,
        measure="nrEvents",
        color_code=measure_colors["nrEvents"],
        category_value="Yemen",
        events_dict=events_dict,
    )
)

Loading BokehJS ...

**Reported attacks in the Red Sea region, particularly in Yemen, have markedly risen since the onset of the conflict in the Middle East.** 

The death toll since April has risen from 11 fatalities in the Red Sea region to 14. The conflict events have risen from 82 to 199. The previous peak seen in March 2024 has been replaced by a new peak in June 2024 which registered 34 conflict events. In the entire region, the number of Houthi-related deaths are 1753 and number of conflict events are 1947 since October 2023. 


---------------
**Updates from April 2024**

Since the start of the Red Sea Crisis on November 17, 2023, until April 11, 2024, 82 conflict events have occurred in the Red Sea region, resulting in 11 fatalities. The conflict events have increased, with March 2024 registering 27 conflict events, the highest so far. These events include anti-ship ballistic missiles launched by Houthi forces and interception and strike efforts by the US, UK, German, French, and Italian Navies. Overall, conflict events involving Houthi forces have resulted in 956 conflict events and 959 conflict-related fatalities across the MENA (Middle East and North Africa) region since the start of the conflict in Gaza.  

In [103]:
def categorize_attacks(texts):
    """
    Categorizes each text in the list based on the presence of the words 'tanker' or 'cargo'.

    Args:
        texts (list): A list of strings where each string represents a text.

    Returns:
        list: A list of categories ('tanker', 'cargo', or 'neither') corresponding to each text.
    """

    if "tanker" in texts.lower():
        return "tanker-related"
    elif "cargo" in texts.lower():
        return "cargo-related"
    else:
        return "neither"

In [177]:
south_red_sea["attack_type"] = south_red_sea["notes"].apply(
    lambda x: categorize_attacks(x)
)
conflict_red_sea = analysis.get_acled_by_group(
    south_red_sea, ["attack_type", "event_type", "sub_event_type"], freq="D"
)

In [179]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from bokeh.palettes import Category10
from datetime import datetime
import random

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}

measure = "nrEvents"
types = list(conflict_red_sea["attack_type"].unique())

colors = ["#4E79A7", "#F28E2B", "#59A14F"]


show(
    visuals.get_stacked_bar_chart(
        conflict_red_sea,
        f"{measure_names[measure]} related to tanker and cargo ships",
        f"Source: ACLED. Accessed date {datetime.today().date().isoformat()}",
        date_column="event_date",
        categories=types,
        measure=measure,
        category_column="attack_type",
        colors=colors,
        width=1000,
        # events_dict=events_dict
    )
)

Loading BokehJS ...

**There were 34 conflict incidents involving tanker ships and 5 involving cargo ships in the South Red Sea Region starting form October 7th 2023 to October 20th 2024.** 13 of the incidents involving tankers were Shelling/artillery/missile attacks while 6 were Air/drone strikes. The cargo-related incidents also resulted in 2 reported fatalities. 

In [183]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from datetime import datetime

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

conflict_red_sea = analysis.get_acled_by_group(south_red_sea, ["actor1"], freq="D")

measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}

measure = "nrEvents"

types = list(conflict_red_sea["actor1"].unique())

num_event_types = len(types)
if num_event_types < 10:
    # If there are fewer than 10 event types, randomly pick that many colors from Category10[10]
    colors = random.sample(Category10[10], num_event_types)
else:
    # If there are 10 or more event types, use Category10[10] directly
    colors = custom_palette = [
        "#4E79A7",
        "#F28E2B",
        "#59A14F",
        "#E15759",
        "#76B7B2",
        "#EDC949",
        "#AF7AA1",
        "#FF9DA7",
        "#9C755F",
        "#BAB0AC",
        "#5DADEC",
        "#FAA43A",
        "#60BD68",
        "#F17CB0",
    ]


show(
    visuals.get_stacked_bar_chart(
        conflict_red_sea,
        f"{measure_names[measure]} by Primary Actor Involved",
        f"Source: ACLED. Accessed date {datetime.today().date().isoformat()}",
        date_column="event_date",
        categories=types,
        measure=measure,
        category_column="actor1",
        colors=colors,
        # events_dict=events_dict
        width=1100,
    )
)

Loading BokehJS ...

**The USA was involved in 90 conflict incidents in the Red Sea region. Of these, 86 were interceptions.** The breakdown of attacks that are interceptions is shown below. 

In [174]:
df = pd.DataFrame(
    south_red_sea[south_red_sea["notes"].str.contains("Interception")][
        "actor1"
    ].value_counts()
).reset_index()
df.rename(
    columns={"count": "Numbe rof incidents involving interceptions"}, inplace=True
)
df

actor1  \
0   Military Forces of the United States (2021-)   
1              Military Forces of France (2017-)   
2               Military Forces of Italy (2022-)   
3  Military Forces of the United Kingdom (2010-)   
4             Military Forces of Germany (2021-)   
5        Private Security Forces (International)   
6             Military Forces of Denmark (2019-)   
7        Military Forces of Yemen (2017-) Houthi   

   Numbe rof incidents involving interceptions  
0                                           86  
1                                            5  
2                                            4  
3                                            4  
4                                            3  
5                                            2  
6                                            1  
7                                            1

**56 specific ships were identified in the reported conflicts with their IMO numbers.** Some ships were involved in more than one incident. The breakdown of ships is as shown below. The countries to which the ships belong to is difficult to ascertain as differnet databases show different results. 

In [136]:
import re


def extract_imo(text):
    # Regular expression to find the IMO number pattern
    match = re.search(r"\(IMO: \d{7}\)", text)
    if match:
        return match.group(0)  # Returns the text within the brackets
    return None

In [137]:
south_red_sea["IMO"] = south_red_sea["notes"].apply(lambda x: extract_imo(x))

In [203]:
analysis.get_acled_by_group(south_red_sea, ["IMO"])[["IMO", "nrEvents"]].sort_values(
    by="nrEvents", ascending=False
)

IMO  nrEvents
16  (IMO: 9312145)         3
2   (IMO: 9213820)         3
27  (IMO: 9419101)         3
39  (IMO: 9601235)         3
20  (IMO: 9327097)         3
13  (IMO: 9297888)         2
43  (IMO: 9694622)         2
18  (IMO: 9320506)         2
15  (IMO: 9302566)         2
14  (IMO: 9298387)         2
55  (IMO: 9942627)         2
34  (IMO: 9512355)         2
9   (IMO: 9263320)         2
8   (IMO: 9253129)         2
51  (IMO: 9799616)         2
41  (IMO: 9632208)         1
35  (IMO: 9514004)         1
36  (IMO: 9523469)         1
37  (IMO: 9565716)         1
38  (IMO: 9595589)         1
54  (IMO: 9923085)         1
53  (IMO: 9893228)         1
40  (IMO: 9616606)         1
48  (IMO: 9760158)         1
42  (IMO: 9693068)         1
47  (IMO: 9748734)         1
44  (IMO: 9699880)         1
45  (IMO: 9699892)         1
50  (IMO: 9784300)         1
46  (IMO: 9737591)         1
33  (IMO: 9486013)         1
49  (IMO: 9779800)         1
52  (IMO: 9839480)         1
0   (IMO: 9174268)         1
32  (IMO: 9482861)         1
31  (IMO: 9469924)         1
3   (IMO: 9223174)         1
4   (IMO: 9237307)         1
5   (IMO: 9239927)         1
6   (IMO: 9243320)         1
7   (IMO: 9248447)         1
10  (IMO: 9276597)         1
11  (IMO: 9284740)         1
12  (IMO: 9288526)         1
17  (IMO: 9312640)         1
19  (IMO: 9324978)         1
21  (IMO: 9340752)         1
22  (IMO: 9395379)         1
23  (IMO: 9398280)         1
24  (IMO: 9400112)         1
25  (IMO: 9402469)         1
26  (IMO: 9402471)         1
1   (IMO: 9184938)         1
29  (IMO: 9437684)         1
30  (IMO: 9461489)         1
28  (IMO: 9426051)         1

In [50]:
conflict_by_country = (
    data.groupby(["country", pd.Grouper(key="event_date", freq="W")])["fatalities"]
    .agg(["sum", "count"])
    .reset_index()
)
conflict_by_country.rename(
    columns={"sum": "nrFatalities", "count": "nrEvents"}, inplace=True
)

In [151]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from bokeh.models import TabPanel

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

conflict_by_country = conflict_by_country.sort_values(by="country", ascending=False)

tabs = []
measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}
# acled_adm0 = get_acled_by_admin(syria_adm2_crs, acled, columns = ['ADM2_EN', 'ADM1_EN'])
for country in list(conflict_by_country["country"].unique()):
    tabs.append(
        TabPanel(
            child=visuals.get_bar_chart(
                conflict_by_country,
                f"Weekly Conflict Event Trend in {country}",
                "Source: ACLED",
                subtitle="",
                category="country",
                measure="nrEvents",
                color_code=measure_colors["nrEvents"],
                category_value=country,
                events_dict=events_dict,
            ),
            title=country.title(),
        )
    )

tabs = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs, warn_on_missing_glyphs=False)

Loading BokehJS ...

In [97]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from bokeh.models import Tabs

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

conflict_by_country = conflict_by_country.sort_values(by="country", ascending=False)

tabs = []
measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}
# acled_adm0 = get_acled_by_admin(syria_adm2_crs, acled, columns = ['ADM2_EN', 'ADM1_EN'])
for country in list(conflict_by_country["country"].unique()):
    tabs.append(
        TabPanel(
            child=visuals.get_bar_chart(
                conflict_by_country,
                f"Weekly Conflict Fatality Trend in {country}",
                "Source: ACLED",
                subtitle="",
                category="country",
                measure="nrFatalities",
                color_code=measure_colors["nrFatalities"],
                category_value=country,
                events_dict=events_dict,
            ),
            title=country.title(),
        )
    )

tabs = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs, warn_on_missing_glyphs=False)

Loading BokehJS ...

In [83]:
conflict_by_country.to_csv(
    "../../data/conflict/conflict_by_country_2023-01-01_2024-10-01.csv"
)
conflict_by_port.to_csv(
    "../../data/conflict/conflict_by_port_2023-01-01_2024-10-01.csv"
)
data.to_csv("../../data/conflict/acled_raw_2023-01-01_2024-10-01.csv")